In [1]:
import pymongo
from   pymongo import MongoClient
from   pymongo import IndexModel

import glob, io, os, json
import pydicom
import numpy as np

import RoomOfRequirement
from RoomOfRequirement.Quad import QUAD_Manager
from RoomOfRequirement.ImageOrganizer import ImageOrganizer
from RoomOfRequirement.Evaluation import Evaluation
from RoomOfRequirement.Case import Case

db = QUAD_Manager()

#DICOMS#
#Note: Dicoms need to be sorted by folder structure: StudyUID - SOPInstanceUID.dcm
#Put in Path to Dicoms (in which folders with StudyUIDs are)
path_to_dcms = '/Users/cmrt/Documents/LGE/EMIDEC Datasets/Emidec dataset (100 cases, 67p, 33h)/IMGS for Lumos'
dcms = glob.glob(path_to_dcms + '//**/*.dcm', recursive = True)
studyuids = set()
for file in dcms: 
    head, suid = os.path.split(os.path.dirname(file))
    try:
        db.insert_dicom_folder(os.path.dirname(file))
    except:
        continue
    dcm = pydicom.dcmread(file)
    studyuids.add(dcm.StudyInstanceUID)
studyuid_list = list(studyuids)

for file in dcms:
    db.dcm_coll.update_one({'path': file},{ "$set": { 'stack_nr': 0 } })


#COHORT
#db.coho_coll.insert_one({'name': 'EMIDEC', 'owner': 'owner', 'ownername': 'ownername', 'studyuids': studyuid_list})
db.insert_cohort({'name': 'EMIDEC', 'owner': 'owner', 'ownername': 'ownername', 'studyuids': studyuid_list})

#TASKS
task_dict1 = {'displayname' :'EMIDEC', 'studyuids': []}
task_dict2 = {'displayname' :'FWHM', 'studyuids': []}
task_dict3 = {'displayname' :'2SD', 'studyuids': []}
task_dict4 = {'displayname' :'3SD', 'studyuids': []}
task_dict5 = {'displayname' :'4SD', 'studyuids': []}
task_dict6 = {'displayname' :'5SD', 'studyuids': []}
task_dict7 = {'displayname' :'6SD', 'studyuids': []}
task_dict8 = {'displayname' :'7SD', 'studyuids': []}

db.insert_task_environment(task_dict1)
db.insert_task_environment(task_dict2)
db.insert_task_environment(task_dict3)
db.insert_task_environment(task_dict4)
db.insert_task_environment(task_dict5)
db.insert_task_environment(task_dict6)
db.insert_task_environment(task_dict7)
db.insert_task_environment(task_dict8)


#CASES
for suid in studyuid_list:       
    case_ = Case(db, suid)
    #case_.get_patient_info()
    #case_dict= {'studyuid': suid, 'name': str(name_dict[suid]), 'age': '', 'gender': '', 'weight': '', 'height': '' }
    #db.case_coll.insert_one(case_dict)
    db.insert_case(case_)

#ANNOS
#Note: Annotations need to be sorted by folder structure: Taskname (folder names == EMIDEC, FWHM, 2SD, 3SD, 4SD, 5SD, 6SD, 7SD) - StudyUID - SopInstanceUID.json
#Fill in Path to where annotations are stored (in which folders with tasknames are)
path_to_annos = '/Users/cmrt/Documents/LGE/EMIDEC Datasets/emidec annos lumos updated slicelocs'
jsons_path = glob.glob(path_to_annos + '//**/*.json', recursive = True)



for j in jsons_path:
    head, suid = os.path.split(os.path.dirname(j))
    sop  = os.path.basename(j).replace('.json','')
    json_anno = json.load(io.open(j))
    h, method = os.path.split(head)
    task = db.task_coll.find({'displayname': method})
    for t in task:
        t['studyuids'].append(suid)
        db.task_coll.update_one({'displayname': method},{ "$set": { 'studyuids': list(set(t['studyuids'])) } })
        task_id = t['_id']
    db.insert_anno(json_anno, task_id, suid, sop)
    

#IMAGE ORGANIZERS 
for suid in studyuid_list:
    sops = db.dcm_coll.find({'studyuid': suid})
    sops_list = []
    for s in sops:
        sops_list.append(s['sop'])
    imgo = ImageOrganizer(db, suid, 'LGE SAX', 0)
    imgo.organize(sops_list)
    db.insert_img_o(imgo)

#EVALUATIONS
for suid in studyuid_list:   
    for method in ['EMIDEC', 'FWHM', '2SD', '3SD', '4SD', '5SD', '6SD', '7SD']: #or what your tasks are named
        tasks = db.task_coll.find({'displayname': method})
        for t in tasks:
            task_id = t['_id']
            if suid in t['studyuids']:
                try:
                    eval_   = Evaluation(db, task_id=task_id, studyuid=suid, imagetype='SAX LGE', stack_nr=0)
                    eval_.evaluate()
                    db.insert_eval(eval_)
                except:
                    continue
   

Traceback (most recent call last):
  File "/Users/cmrt/Documents/Lumos/src/RoomOfRequirement/Quad.py", line 131, in insert_dicom_folder
    quad.dcm_coll.insert_one(dcmjson)
  File "/Users/cmrt/anaconda3/envs/TestInstall/lib/python3.12/site-packages/pymongo/synchronous/collection.py", line 891, in insert_one
    self._insert_one(
  File "/Users/cmrt/anaconda3/envs/TestInstall/lib/python3.12/site-packages/pymongo/synchronous/collection.py", line 831, in _insert_one
    self._database.client._retryable_write(
  File "/Users/cmrt/anaconda3/envs/TestInstall/lib/python3.12/site-packages/pymongo/synchronous/mongo_client.py", line 1898, in _retryable_write
    return self._retry_with_session(retryable, func, s, bulk, operation, operation_id)
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/Users/cmrt/anaconda3/envs/TestInstall/lib/python3.12/site-packages/pymongo/synchronous/mongo_client.py", line 1784, in _retry_with_session
    return self._ret

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



Traceback (most recent call last):
  File "/Users/cmrt/Documents/Lumos/src/RoomOfRequirement/Quad.py", line 131, in insert_dicom_folder
    quad.dcm_coll.insert_one(dcmjson)
  File "/Users/cmrt/anaconda3/envs/TestInstall/lib/python3.12/site-packages/pymongo/synchronous/collection.py", line 891, in insert_one
    self._insert_one(
  File "/Users/cmrt/anaconda3/envs/TestInstall/lib/python3.12/site-packages/pymongo/synchronous/collection.py", line 831, in _insert_one
    self._database.client._retryable_write(
  File "/Users/cmrt/anaconda3/envs/TestInstall/lib/python3.12/site-packages/pymongo/synchronous/mongo_client.py", line 1898, in _retryable_write
    return self._retry_with_session(retryable, func, s, bulk, operation, operation_id)
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/Users/cmrt/anaconda3/envs/TestInstall/lib/python3.12/site-packages/pymongo/synchronous/mongo_client.py", line 1784, in _retry_with_session
    return self._ret

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



Traceback (most recent call last):
  File "/Users/cmrt/Documents/Lumos/src/RoomOfRequirement/Quad.py", line 131, in insert_dicom_folder
    quad.dcm_coll.insert_one(dcmjson)
  File "/Users/cmrt/anaconda3/envs/TestInstall/lib/python3.12/site-packages/pymongo/synchronous/collection.py", line 891, in insert_one
    self._insert_one(
  File "/Users/cmrt/anaconda3/envs/TestInstall/lib/python3.12/site-packages/pymongo/synchronous/collection.py", line 831, in _insert_one
    self._database.client._retryable_write(
  File "/Users/cmrt/anaconda3/envs/TestInstall/lib/python3.12/site-packages/pymongo/synchronous/mongo_client.py", line 1898, in _retryable_write
    return self._retry_with_session(retryable, func, s, bulk, operation, operation_id)
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/Users/cmrt/anaconda3/envs/TestInstall/lib/python3.12/site-packages/pymongo/synchronous/mongo_client.py", line 1784, in _retry_with_session
    return self._ret

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



<class 'RoomOfRequirement.Quad.QUAD_Manager'>
1.2.826.0.1.3680043.8.498.84025865368102386298694817914264092614 LGE SAX 0
here auch None
'FileDataset' object has no attribute 'MagneticFieldStrength'
'FileDataset' object has no attribute 'SoftwareVersions'
'FileDataset' object has no attribute 'FlipAngle'
'FileDataset' object has no attribute 'ManufacturerModelName'
'FileDataset' object has no attribute 'InstitutionalDepartmentName'
<class 'RoomOfRequirement.Quad.QUAD_Manager'>
1.2.826.0.1.3680043.8.498.57691103543274403548360383164120062582 LGE SAX 0
here auch None
'FileDataset' object has no attribute 'MagneticFieldStrength'
'FileDataset' object has no attribute 'SoftwareVersions'
'FileDataset' object has no attribute 'FlipAngle'
'FileDataset' object has no attribute 'ManufacturerModelName'
'FileDataset' object has no attribute 'InstitutionalDepartmentName'
<class 'RoomOfRequirement.Quad.QUAD_Manager'>
1.2.826.0.1.3680043.8.498.52850454907088770050887114952706654452 LGE SAX 0
here auch

In [8]:
from   pymongo import MongoClient
from   pymongo import IndexModel

import glob, io, os, json
import pydicom
import numpy as np

import RoomOfRequirement
from RoomOfRequirement.Quad import QUAD_Manager
from RoomOfRequirement.ImageOrganizer import ImageOrganizer
from RoomOfRequirement.Evaluation import Evaluation
from RoomOfRequirement.Case import Case

db = QUAD_Manager()

#DICOMS#
#Note: Dicoms need to be sorted by folder structure: label - StudyUID - SOPInstanceUID.dcm
#Put in Path to Dicoms (in which folders with StudyUIDs are)
path_to_dcms = '/Users/cmrt/Documents/Quad_ImagetypesProject/Extended_Classes_111224_Train'
dcms = glob.glob(path_to_dcms + '//**/*.dcm', recursive = True)
studyuids = set()
for file in dcms: 
    sop = os.path.basename(file).replace('.dcm','')
    head, suid = os.path.split(os.path.dirname(file))
    label = os.path.basename(head)
    
    #try:
    #    db.insert_dicom_folder(os.path.dirname(file))
    #except:
    #    continue
    db.dcm_coll.update_one({'sop': sop},{ "$set": { 'imagetype': label } })

#for file in dcms:
#    db.dcm_coll.update_one({'path': file},{ "$set": { 'stack_nr': 0 } })